# Exploratory Data Analysis - US Warehouses

<p><a name="sections"></a></p>


## Sections

- <a href="#preprocess">Preprocessing \& Enrichment </a><br>
 - <a href="#clean">Cleaning</a><br>
 - <a href="#readin">Read in External Datasets</a><br>
   - <a href="#cities">Latitude and Longitude : Cities</a><br>
   - <a href="#airports">Latitude and Longitude : Airports</a><br>
   - <a href="#ports">Latitude and Longitude : Ports</a><br>
   - <a href="#regions">Regional Assignments</a><br>
   - <a href="#merge1">Merge Location Information</a><br>
 - <a href="#createtrans">Create Transport Dictionary</a><br>
    - <a href="#transAnalysis">City Transport Analysis</a><br>
 - <a href="#cityprice">Aggregation: City Level</a><br>
     - <a href="#outlier1">Outlier Analysis</a><br>
     - <a href="#merge2">Merge with Transport Dataframe</a><br>
 - <a href="#connectivity">Connectivity Metric</a><br>
 - <a href="#connect+">Connect+ Metric</a><br>
- <a href="#visual">Analysis</a><br>
 - <a href="#city_vis">City Level</a><br>
 - <a href="#tristate">NY Metro Case Study</a><br>
    - <a href="#nylease">Lease Rates Across Different Sizes</a><br>
 - <a href="#statelevel">State Level Analysis</a><br>

In [1]:
%load_ext autoreload
%autoreload 2

import pandas as pd
import numpy as np
import re
from clean import *
pd.set_option('display.max_columns', 50)

<p><a name="preprocess"></a></p>

## Preprocessing

Write all csv files in the data folder to text file in current directory

In [2]:
!ls ./data > data.txt

#### Read in data.txt and create dataframe df from raw data

In [3]:
with open('data.txt','r') as f:
    lines = f.readlines()

data = []   
for line in lines:
    data.append(pd.read_csv('./data/'+line[:-1]))

df_raw = pd.concat(data)

<p><a name="clean"></a></p>

### Cleaning

Clean and generate new columns with clean.py and export cleaned data to csv

In [4]:
df = clean(df_raw)
df.to_csv('data_cleaned.csv')
df.shape
df = df.dropna(subset=['price'])
df.shape

(11813, 16)

(9217, 16)

<p><a name="readin"></a></p>

### Read in External Datasets

Read in external datasets for richer data analysis and exploration

<p><a name="cities"></a></p>

#### Latitude and Longitude: Cities

In [5]:
latlon = pd.read_csv('./extra-data/us-zip-geom.csv', 
                     header=0, 
                     names = ['city','state','lat','lon'],
                     usecols = [1,2,3,4],
                    index_col=False)

# Artifact from cities with multiple zipcodes. 
latlon = latlon.drop_duplicates(subset=['city'])

In [6]:
latlon[latlon.city=='Brookfield']

city state        lat       lon
356  Brookfield    OH  41.239987 -80.58346

<p><a name="airports"></a></p>

#### Latitude and Longitude: Airports

Read in airport dataset. I'll only use large and medium sized airports, ignoring small private airfields and heliports that are not usually considered for most supply chain analyses


In [7]:
airports = pd.read_csv('./extra-data/us-airports.csv')
airports = airports[airports['type'].isin(['large_airport','medium_airport'])]
airports = airports[['type','name','latitude_deg','longitude_deg','iso_region']]
airports['iso_region'] = airports['iso_region'].apply(lambda x: x[-2:])
airports.columns = ['type','name','lat','lon','state']
airports.dropna(inplace=True)
airports = airports[:300]

In [8]:
airports.sample()

type                name        lat         lon state
126  medium_airport  Centennial Airport  39.570099 -104.848999    CO

<p><a name="ports"></a></p>

#### Latitude and Longitude: Ports

Read in port dataset. Select for US ports.

In [9]:
ports = pd.read_json('./extra-data/ports.json', orient='index')
ports = ports[['name','coordinates','city','province','country']]

ports = ports[ports.country=='United States']
ports = ports.reset_index()

tags = ports['coordinates'].apply(pd.Series)
ports = pd.concat([ports,tags],axis=1)
ports = ports.drop(['index','city','country','coordinates'], axis=1)
ports.columns = ['name','state','lon','lat']
ports.dropna(inplace=True)
ports['name'] += ' Port'

In [10]:
ports.sample()

name     state        lon        lat
93  Peoria Port  Illinois -89.588986  40.693649

<p><a name="regions"></a></p>

#### Regional Assignments

Read in regional and divisional assignments for each state according to the US Census Bureau

In [11]:
regions = pd.read_csv('./extra-data/states.csv')

<p><a name="merge1"></a></p>

#### Merge Location Information

Merge warehouse data with city level latitude and longitude data and regional assignments on the state level. 

In [12]:
df_ = pd.merge(df, latlon, on=['city','state'], how='left')
df = pd.merge(df_,regions[['State Code','Region','Division']], how='left',left_on='state',right_on='State Code')
df.drop(columns = ['State Code'], inplace=True)

In [13]:
df.sample()

address  buildingSize     city listingDate  price  \
4499  2600 W 35th St Chicago, IL      688000.0  Chicago  2010-09-24    0.5   

        propType  spaceAvailable  spaces state             subType  \
4499  Industrial          230000       3    IL  Office, Industrial   

                                              transport  \
4499  {'Western Avenue Station (BNSF) Commuter Rail ...   

                                    utilities  yearBuilt  yearRenovated  \
4499  [Lighting, Halide, Gas, Heating, Sewer]       1930           1958   

                                               propInfo  ceilingHeight  \
4499    lease rate does not include utilities, prope...             16   

            lat       lon   Region            Division  
4499  41.901485 -87.74055  Midwest  East North Central

<p><a name="createtrans"></a></p>

### Create Transport Hub Dataframe

For all transportation connections pulled in from the listing, I aggregate the speedOfTravel (calculated by dividing the distance by time (converted to hours) to get an estimated measure of traffic/congestion in that area.

<img src="./pics/transport_example.png">

In [14]:
# Create an empty list to house the extracted values
lst = []
# Enumerate for every dictionary entry in the transport column
for i,dic in enumerate(df.transport):
    state, city, lat,lon = df.iloc[i][['state','city','lat','lon']]
    city = city + ', ' + state
    for k,v in dic.items():
        lst.append([i, state, city, lat,lon, k, *v])

transport_df = pd.DataFrame(lst, columns=['index','state','city','lat','lon', 'name','distance','timeTo','speedOfTravel'])

The new dataframe, **transport_df**, preserves the index of the entry it's tied to in the original dataframe, **df**

\*Note\* In this case the geom point corresponds to the city not the 'name' of the transportation hub

In [15]:
transport_df.head(5)

index state            city        lat       lon  \
0      0    NC   Charlotte, NC  35.248292 -80.82748   
1      0    NC   Charlotte, NC  35.248292 -80.82748   
2      0    NC   Charlotte, NC  35.248292 -80.82748   
3      1    NC  Greensboro, NC        NaN       NaN   
4      1    NC  Greensboro, NC        NaN       NaN   

                                                name  distance  timeTo  \
0            Charlotte Douglas International Airport       8.7    20.0   
1                                 Port of Wilmington     205.6   244.0   
2  NS THOROUGHBRED BULK TRANSFER TERMINAL-CHARLOT...       0.5     2.0   
3               Piedmont Triad International Airport       9.7    20.0   
4                 Virginia Port Authority - Richmond     206.8   241.0   

   speedOfTravel  
0           26.1  
1           50.6  
2           15.0  
3           29.1  
4           51.5

Create a new dataframe for the average traffic in each city. 

This dataset contains many cities containing only one warehouse. While at first glance this could be seen to present a problem - I make the following assumptions to justify aggregation by mean for a traffic metric:

1. Cities with few warehouse listings probably don't have much traffic regularly and so one or two datapoints isn't a problem.

2. One warehouse can have multiple entries for nearby transport hubs, allowing for a better sense of local traffic even with a single listing.

3. Information is self reported by each realtor, to market the listing attractively and include as many relevant hubs as possible. 

In [16]:
traffic_city = transport_df.groupby(['city','state','lat','lon']).agg({'city': 'count',
                                                   'distance': 'mean',
                                                   'timeTo' : 'mean',
                                                   'speedOfTravel': 'mean'}).round(0)
traffic_city.columns = ['datapoints','distance','time','speed']
traffic_city = traffic_city.reset_index()

All calculated values are averages. 

Average distance is in miles.

Average travel time to nearest transportation (airport, freight port, railroad, etc.) is in minutes. 

Average speed is in MPH. (Calculated in the clean.py file)

All values rounded to nearest unit. 

In [17]:
traffic_city.sample(2)

city state        lat         lon  datapoints  distance  time  \
579   La Habra, CA    CA  33.640302 -117.769442          14      16.0  25.0   
467  Hauppauge, NY    NY  40.810246  -73.191789          23      18.0  26.0   

     speed  
579   35.0  
467   34.0

<p><a name="transAnalysis"></a></p>

#### City Transport Analysis

Now, lets look for cities with an average speed over 3 standard deviations away. 

In [18]:
from scipy import stats
traffic_city[np.abs(stats.zscore(traffic_city[['speed']]) > 3).all(axis=1)]

city state        lat        lon  datapoints  distance   time  \
402  Gillette, WY    WY  43.939968 -105.52445           3     113.0  120.0   

     speed  
402   57.0

Basically none! I had a problem earlier with calculated speeds of over 1000 MPH and the problem was many listings had travel time information that simply did not agree with the capabilites of modern automotive engineering. It turned out my assumption of realtor honesty was slightly misplaced. There's no way you can go 20 miles in one minute. I cleaned up that problem in clean.py where I set a maximum speed limit of 75MPH.

<img src="./pics/crazySpeed.png">

<p><a name="cityprice"></a></p>

### Aggregation: City Level

Aggregate listings by cities, counting the number of warehouses in each city, and taking the mean or median values of various features. 

In [19]:
# Rename city column to account for shared city names among states
df['city'] = df['city'] + ', ' + df['state']
price_df = df.groupby(['city','state','Region','Division']).agg({'address' : 'count',
                         'price' : 'mean',
                         'spaceAvailable' : 'median',
                         'buildingSize' : 'median',
                         'yearBuilt' : 'median',
                         'yearRenovated' : 'median'
                         })

price_df = price_df.reset_index()
price_df.columns = ['city','state','region','division',\
                    'warehouses','price','leaseSpace',\
                    'buildingSize','yearBuilt','yearRenovated']

price_df.price = price_df.price.round(2)
price_df.leaseSpace = price_df.leaseSpace.round(-2) # round to nearest 100
price_df.buildingSize = price_df.buildingSize.round(-2)
price_df.yearBuilt = price_df.yearBuilt.astype(int)
price_df.yearRenovated = price_df.yearRenovated.astype(int)

In [20]:
price_df.sample(2)

city state region        division  warehouses  price  \
1436  Middletown, DE    DE  South  South Atlantic           2   0.86   
501       Cotati, CA    CA   West         Pacific           1   1.30   

      leaseSpace  buildingSize  yearBuilt  yearRenovated  
1436      8600.0       19700.0       2013           2013  
501      23000.0       45000.0       2019           2019

<p><a name="outlier1"></a></p>

#### Outlier Analysis

Plenty of outliers in this set. 

Takeaway: New York and LA real estate is very expensive. And Newark Ohio too

In [21]:
price_df[np.abs(stats.zscore(price_df[['price']]) > 4).all(axis=1)]

city state     region            division  warehouses  \
752        Flushing, NY    NY  Northeast     Middle Atlantic           3   
1511  Mountain View, CA    CA       West             Pacific           2   
1556      New Lenox, IL    IL    Midwest  East North Central           4   
1567       New York, NY    NY  Northeast     Middle Atlantic           2   
1570         Newark, OH    OH    Midwest  East North Central           1   
1702      Palo Alto, CA    CA       West             Pacific           1   
1999   Santa Monica, CA    CA       West             Pacific           3   
2242         Tunica, MS    MS      South  East South Central           1   
2468        Woodway, TX    TX      South  West South Central           2   

      price  leaseSpace  buildingSize  yearBuilt  yearRenovated  
752    2.64      4500.0       15000.0       1949           1949  
1511   2.92      5100.0       12100.0       1970           1970  
1556   3.54      1900.0        9600.0       1993           1993  
1567   5.44      1700.0       14500.0       1976           1976  
1570  11.85     20000.0      172100.0       1954           1954  
1702   2.75      6600.0        6600.0       1963           1963  
1999   5.08      3000.0       14900.0       1960           1960  
2242   3.00     11000.0       11000.0       1980           1980  
2468   2.91      9700.0       31900.0       1971           1971

Nothing truly unexpected except for Newark OH, so we're just going to drop that one

In [22]:
price_df = price_df.drop(labels=1570)

<p><a name="merge2"></a></p>

#### Merge with Transport Dataframe

In [56]:
mean_df = pd.merge(price_df, traffic_city, 
                   on = ['city','state'],
                   how = 'inner')


<p><a name="connectivity"></a></p>

### Connectivity Metric

Create new column for connectivity.

Connectivity is the density of connections in a given city divided by the average time (hrs) to travel to those connections.

I use this measure since it ignores traffic conditions that could affect using the average distance in the calculation. Traveling 10 miles in NYC is very different than traveling 10 miles in Alaska.

In [118]:
mean_df['hubDensity'] = mean_df['datapoints'] / mean_df['warehouses']
mean_df['connectivity'] = (mean_df['hubDensity']*60/mean_df['time']).round(2)

# Normalization
mean_df['connectivity'] /= np.max(mean_df['connectivity'],axis=0)/100
mean_df['connectivity'] = mean_df['connectivity'].round(0)

<p><a name="connect+"></a></p>

### Connect+ Metric

In [58]:
cities = mean_df[['city','lat','lon']]
cities.columns = ['name','lat','lon']

ports = ports[['name','lat','lon']]
airports = airports[['name','lat','lon']]



The following cell calculates the distance between every city, port, and airport in this notebook.

It may take a while. So I've included the data in the folder from a previous session. 

In [59]:
from wh_metrics import *

#distMatrix = distance_matrix([cities,ports,airports])
#distMatrix.to_csv('./extra-data/distances.csv')
#distMatrix = pd.read_csv('./extra-data/distances.csv').drop(columns='Unnamed: 0')
distMatrix.head(5)


Abbotsford, WI  Abilene, TX  Abingdon, MD   Abrams, WI      Ada, OK  \
0        0.000000  1002.904166    808.998227   111.204134   779.276978   
1     1002.904166     0.000000   1393.291343  1060.322894   240.191915   
2      808.998227  1393.291343      0.000000   704.065660  1165.027547   
3      111.204134  1060.322894    704.065660     0.000000   828.539959   
4      779.276978   240.191915   1165.027547   828.539959     0.000000   

   Adairsville, GA  Adelanto, CA   Agawam, MA     Aiea, HI    Aiken, SC  \
0       784.715228   1599.776619   906.276134  4106.689541   907.285702   
1       863.504771   1034.696110  1624.268592  3623.318685  1050.976242   
2       592.381527   2276.687984   263.065520  4860.060420   498.736576   
3       738.751755   1703.409315   795.113289  4217.561298   842.338569   
4       667.980445   1181.976144  1389.844170  3790.122836   862.385720   

   Airway Heights, WA    Akron, OH   Albany, NY  Albert Lea, MN  \
0         1308.899874   514.992252   829.126323      176.090003   
1         1408.049431  1169.371884  1569.078440      849.690887   
2         2115.909580   298.874627   248.587889      926.549682   
3         1417.486812   414.703762   717.926665      275.013213   
4         1397.218321   931.771058  1332.828055      638.190364   

   Albuquerque, NM    Allen, KY  Allentown, PA  Alpharetta, GA   Alsip, IL  \
0      1100.535510   641.294630     805.770566      818.258398  260.613814   
1       438.924354  1024.983502    1456.504376      901.052431  918.756947   
2      1689.880957   370.276269      94.927743      576.676789  618.508598   
3      1190.346177   567.524691     697.022586      768.229325  215.670001   
4       567.321492   800.658322    1224.378002      709.244143  679.306750   

     Alvin, TX  Amarillo, TX  American Fork, UT  Amesbury, MA  Anaheim, CA  \
0  1107.016710    908.212365        1132.352871    972.701076  1652.354988   
1   336.499136    229.679536         867.653481   1721.385879  1058.288604   
2  1279.937452   1430.983398        1868.964121    363.692669  2320.459410   
3  1132.977027    984.922093        1240.728603    861.700494  1755.202541   
4   379.577367    297.055416         913.462451   1485.931319  1214.613123   

   Anamosa, IA  ...  Cedar City Regional Airport  \
0   202.418910  ...                  1278.853459   
1   814.425972  ...                   839.309177   
2   803.166347  ...                  1977.489508   
3   246.106142  ...                  1383.824801   
4   584.317691  ...                   936.796236   

   Fayetteville Regional Grannis Field  Valley International Airport  \
0                           914.413200                   1356.465669   
1                          1208.962387                    444.695622   
2                           340.701634                   1534.088412   
3                           832.084904                   1389.226691   
4                          1006.635824                    593.283214   

   Helena Regional Airport  Tweed New Haven Airport  Willow Run Airport  \
0              1047.527756               912.770815          387.188257   
1              1175.781192              1596.887810         1115.996855   
2              1850.805378               218.019963          423.256144   
3              1157.487475               802.064956          286.715018   
4              1141.875966              1364.441842          875.924726   

   Mc Minnville Municipal Airport  \
0                     1590.932235   
1                     1530.357998   
2                     2390.478230   
3                     1701.269931   
4                     1565.743372   

   Jack Northrop Field Hawthorne Municipal Airport  Chicago Executive Airport  \
0                                      1666.962066                 229.993223   
1                                      1080.186149                 932.165166   
2                                      2338.733185                 633.179067   
3                     

#### Metric: Average Distance to n Closest Neighbors

In [60]:
# Merge to get additional metric of average distance to n nearest neighbors
# in this case n = 20
neighbors = n_nearest(distMatrix, 20).round(0)
df_ = pd.merge(mean_df,neighbors[['name','mean_dist']], \
                   left_on='city',right_on='name', how='left')

#### Metric: Number of Nearest for a given Distance

In [61]:
num_near = num_nearest(distMatrix,d=30)
mean_df = pd.merge(df_,num_near[['name','num_nearest']], \
                   left_on='city',right_on='name', how='left')
mean_df.drop(columns=['name_x','name_y'], inplace=True)

In [103]:
mean_df.sample()

city state region        division  warehouses  price  \
181  Charlotte, NC    NC  South  South Atlantic          76   0.59   

     leaseSpace  buildingSize  yearBuilt  yearRenovated        lat       lon  \
181     24000.0       80000.0       1989           1992  35.248292 -80.82748   

     datapoints  distance  time  speed  hubDensity  connectivity  mean_dist  \
181         169      71.0  89.0   33.0    2.223684           1.5       30.0   

     num_nearest  connect+  
181           13       0.8

#### Connect+ Calculation

In [79]:
mean_df['connect+'] = mean_df['connectivity']*(1+mean_df['num_nearest']**2)/mean_df['mean_dist']
mean_df.sample(4)

city state     region            division  warehouses  price  \
884  Pflugerville, TX    TX      South  West South Central           1   0.79   
115     Boyertown, PA    PA  Northeast     Middle Atlantic           2   0.35   
280        Durham, NC    NC      South      South Atlantic           3   0.78   
926    Quakertown, PA    PA  Northeast     Middle Atlantic           3   0.46   

     leaseSpace  buildingSize  yearBuilt  yearRenovated        lat       lon  \
884      6800.0        6800.0       2003           2003  30.450122 -97.62300   
115     11100.0       58300.0       1927           1986  40.338497 -75.66320   
280      7100.0        7100.0       1996           1996  36.015992 -78.95911   
926    116600.0      116600.0       1999           1999  40.445203 -75.34838   

     datapoints  distance  time  speed  hubDensity  connectivity  mean_dist  \
884           5      42.0  59.0   35.0    5.000000          17.0       64.0   
115           8      27.0  47.0   35.0    4.000000          17.0       18.0   
280           9      63.0  77.0   43.0    3.000000           8.0       46.0   
926          10      26.0  42.0   35.0    3.333333          16.0       16.0   

     num_nearest    connect+  
884            5    6.906250  
115           25  591.222222  
280            5    4.521739  
926           25  626.000000

#### How best to Normalize this?

In [80]:
mean_df['connect+'].std()

9780.543177685959

In [119]:
mean_df['connect+'] = mean_df['connectivity'] + mean_df['num_nearest']
mean_df['connect+'] /= np.max(mean_df['connect+'],axis=0)/100
mean_df['connect+'] = mean_df['connect+'].round(1)

In [120]:
mean_df.head()

city state   region            division  warehouses  price  \
0  Abbotsford, WI    WI  Midwest  East North Central           1   0.36   
1     Abilene, TX    TX    South  West South Central           3   0.52   
2    Abingdon, MD    MD    South      South Atlantic           1   0.54   
3      Abrams, WI    WI  Midwest  East North Central           1   0.34   
4         Ada, OK    OK    South  West South Central           1   0.50   

   leaseSpace  buildingSize  yearBuilt  yearRenovated        lat        lon  \
0     17200.0       17200.0       1970           1970  44.950905 -90.304860   
1      3800.0       20000.0       1984           1984  32.407690 -99.721070   
2     60000.0       60600.0       1995           1995  39.473899 -76.298300   
3      4100.0        4100.0       1986           1986  44.788898 -88.045350   
4     60000.0       60000.0       1940           1940  34.772557 -96.661745   

   datapoints  distance   time  speed  hubDensity  connectivity  mean_dist  \
0           1      24.0   39.0   37.0         1.0           5.0       84.0   
1           6     138.0  172.0   43.0         2.0           2.0      133.0   
2           2       6.0   12.0   30.0         2.0          33.0       32.0   
3           2      21.0   32.0   40.0         2.0          12.0       64.0   
4           2     176.0  225.0   47.0         2.0           2.0       97.0   

   num_nearest  connect+  
0            0       2.8  
1            1       1.7  
2            7      22.5  
3            3       8.4  
4            0       1.1

<p><a name="visual"></a></p>

## Analysis

In [121]:
import pandas as pd
from sklearn import preprocessing
columns = ['price', 'leaseSpace', 'buildingSize', 'yearBuilt',\
           'yearRenovated', 'lat','lon','hubDensity','connectivity',\
           'mean_dist', 'num_nearest', 'connect+']
df_ = mean_df[columns]
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(df_)
df_ = pd.DataFrame(x_scaled, columns = columns)

In [133]:
df_.corr()[np.abs(df_.corr()) > 0.3]['price']

price            1.000000
leaseSpace            NaN
buildingSize          NaN
yearBuilt             NaN
yearRenovated         NaN
lat                   NaN
lon                   NaN
hubDensity       0.348794
connectivity     0.440953
mean_dist             NaN
num_nearest      0.382059
connect+         0.461239
Name: price, dtype: float64

After so much effort, the connect+ metric only improves on connectivity as a metric to gauge price by 0.02.

### Visualization

In [144]:
import chart_studio
import chart_studio.plotly as py
import chart_studio.tools as tls
import plotly.graph_objects as go
from plotly.validators.scatter.marker import SymbolValidator
username = 'snuzbrokh'
key = 'VO2VYRrTv3I0uWHHkUpX'

chart_studio.tools.set_credentials_file(username=username, api_key=key)

<p><a name="city_vis"></a></p>

### National Distribution on City Level

The following is a visualization of the nationwide distribution of warehouses. The location is approximated by the corresponding city coordinates. 

Each "city" is then sorted according to the average rate at which industrial warehouse space is leased. 

The visualization also sizes each city according to the value of the "connectivity" metric I calculated earlier. Cities with higher connectivity have larger circles and ones with lower connectivity have smaller radii. 

Hovering over each circle also reveals the calculated averages for various features of the warehouses in that city: 
- Average distance to the hub (how many miles to the freight port)
- Average time to the hub (how much time to the freight port)
- Average price per square foot
- Median square footage of lease space
- Connectivity of the city

In [145]:
df_ = mean_df.sort_values(by=['price'], ascending = False)

for col in df_.columns:
    df_[col] = df_[col].astype(str)
    
df_['text'] = df_['city'] + \
              '<br>Distance to Hub: ' + df_['distance'] + ' mi'\
              '<br>Time to Hub: ' + df_['time'] + ' min' +\
              '\n<br>Price per SF: $' + df_['price'] + \
              '<br>Square Footage: ' + df_['leaseSpace'] + ' SF' +\
              '<br>Connectivity: ' + df_['connectivity']
limits = [(0,50),(51,500),(501,900),(901,1172),(1173,1273)]
colors = ["purple","crimson","lightseagreen","orange","yellow"]
cities = []
scale = 1.2

# Too many airports for a good visualization
airports = airports[:300]

In [146]:
fig = go.Figure()
for i in range(len(limits)):
    lim = limits[i]
    df_sub = df_[lim[0]:lim[1]]
    fig.add_trace(go.Scattergeo(
        locationmode = 'USA-states',
        lon = df_sub['lon'].astype(float),
        lat = df_sub['lat'].astype(float),
        text = df_sub['text'],
        marker = dict(
            size = df_sub['connectivity'].astype(float)**scale,
            color = colors[i],
            line_color='rgb(40,40,40)',
            line_width=0.5,
            sizemode = 'area'
        ),
        name = '{0} - {1}'.format(lim[0],lim[1])))

# Add in port locations
fig.add_trace(go.Scattergeo(
    locationmode = 'USA-states',
    lon = ports['lon'].astype(float),
    lat = ports['lat'].astype(float),
    text = ports['name'],
    marker = dict(
        size = 4,
        color = 'white',
        line_color = 'rgb(0,0,0)',
        line_width = 1,
        sizemode = 'area'
    ),
    name = 'Ports'))

# Add in airport locations
fig.add_trace(go.Scattergeo(
    locationmode = 'USA-states',
    lon = airports['lon'].astype(float),
    lat = airports['lat'].astype(float),
    text = airports['name'],
    marker = dict(
        size = 10,
        color = 'white',
        line_color = 'blue',
        line_width = 2,
        symbol = 219
    ),
    name = 'Airports'))
fig.update_geos(
    resolution=50,
    showrivers=True, rivercolor="Blue"
)
fig.update_layout(
        title_text = 'Warehouse Connectivity by City \
        <br>(Click legend to toggle traces sorted by price)',
        showlegend = True,
        geo = dict(
            scope = 'usa',
            landcolor = 'rgb(217, 217, 217)',
        )
    )

#### Export Visualization to Plotly

The link below offers a much better user experience for viewing the visualization

In [147]:
py.plot(fig, 
        filename = "city warehouses bubble graph", 
        auto_open = False)

'https://plotly.com/~snuzbrokh/34/'

<p><a name="tristate"></a></p>

### NY Metro Case Study

The New York metropolitan area is the largest metropolitan area in the world by physical size. The metropolitan area includes New York City (the most populous city in the United States), Long Island, and the Mid and Lower Hudson Valley in the state of New York; the five largest cities in New Jersey: Newark, Jersey City, Paterson, Elizabeth, and Edison, and their vicinities; and six of the seven largest cities in Connecticut: Bridgeport, New Haven, Stamford, Waterbury, Norwalk, and Danbury, and their vicinities.

For our purposes we will look at all the warehouses in the 4 state region. 


<p><a name="nylease"></a></p>

#### Distribution of Lease Rates Across Sizes

In [148]:
# Take out outliers like expensive and small warehouse space in Manhattan
df_ = mean_df[mean_df.state.isin(['NY','NJ','CT','PA'])]
nymetro = df_[np.abs(stats.zscore(df_[['price']]) < 3).all(axis=1)]

In [152]:
bins = [0,1e4,5e4,1e9]
nymetro['spaceClass'] = pd.cut(nymetro.leaseSpace,bins,labels=['small','medium','large'])

/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [162]:
fig = px.scatter(nymetro, x='connect+',y='price',
                 facet_col='spaceClass',color='state',
                 hover_data=['city'],
                 size='mean_dist',
                trendline='ols')
fig.show()

In [159]:
py.plot(fig, 
        filename = "price across sizes", 
        auto_open = False)

'https://plotly.com/~snuzbrokh/65/'

### Histograms of Prices

In [176]:
tristate = df[df.state.isin(['NY','NJ','CT','PA'])]

In [177]:


counts, bins = np.histogram(tristate.price,bins=np.linspace(0,7,50))
bins = 0.5*(bins[:-1]+bins[1:])
probs = counts/float(counts.sum())

hist = go.Figure()
hist = px.bar(x=bins, y=probs, labels={'x': 'Price',
                                       # 'y': '% Distribution'})
groups = tristate.groupby('state')
for state, group in groups:
    hist.add_trace(go.Histogram(x=group.price,
                               name=state))
                   
hist.update_layout(
    title_text='Tristate Price Distribution', # title of plot
    xaxis_title_text='Price', # xaxis label
    yaxis_title_text='Count', # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
    bargroupgap=0.1 # gap between bars of the same location coordinates
)

hist.update_traces(opacity=0.90)
hist.show()

### Scatter Matrix

In [294]:
import pandas as pd
from sklearn import preprocessing
columns = ['price','leaseSpace','lat','lon','distance','time','speed','connectivity','hubDensity']
df_ = mean_df[columns]
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(df_)
df_ = pd.DataFrame(x_scaled, columns = columns)

In [165]:
fig = px.scatter_matrix(nymetro, dimensions=['leaseSpace','connect+','num_nearest','price','yearBuilt'], color='state')
fig.show()

<p><a name="statelevel"></a></p>

### State Level Indicators
Here we group on the state level to get similar indications of average speed, distance, and time. It is hoped such data is also useful since most transport hubs are by definition linked to others in the state itself and nearby ones. Another assumption I make is that such networks have been optimzied nationwide so I expect to see not much variation between states in these numbers. 

In [172]:
state_df = mean_df.groupby(['state','region','division']).agg({'city': 'count',
                                                'price' : 'mean',
                                                'leaseSpace' : 'median',
                                                'buildingSize' : 'median',
                                                'yearBuilt' : 'median',
                                                'yearRenovated' : 'median',
                                                'lat' : 'mean',
                                                'lon' : 'mean',
                                                'distance': 'mean',
                                                'time' : 'mean',
                                                'connectivity':'mean',
                                                'connect+' : 'mean',
                                                'hubDensity' : 'mean'})
state_df = state_df.reset_index()
state_df.price = state_df.price.round(2)
state_df.leaseSpace = state_df.leaseSpace.round(-2).astype(int) # round to nearest 100
state_df.buildingSize = state_df.buildingSize.round(-2).astype(int)
state_df.yearBuilt = state_df.yearBuilt.astype(int)
state_df.yearRenovated = state_df.yearRenovated.astype(int)
state_df.connectivity = state_df.connectivity.round(2)
state_df.hubDensity = state_df.hubDensity.round(1)
state_df.distance = state_df.distance.round(0)
state_df.time = state_df.time.round(0)


Outliers on connectivity at the state level:

In [175]:
state_df[np.abs(stats.zscore(state_df[['connectivity']]) > 2).all(axis=1)]

state     region         division  city  price  leaseSpace  buildingSize  \
30    NJ  Northeast  Middle Atlantic    67   0.83       16000         53800   
33    NY  Northeast  Middle Atlantic    60   1.28       10400         30800   

    yearBuilt  yearRenovated        lat        lon  distance  time  \
30       1972           1978  40.555634 -74.391213      16.0  26.0   
33       1968           1969  41.115065 -73.750487      20.0  29.0   

    connectivity   connect+  hubDensity  
30         40.48  52.171642         4.7  
33         40.23  47.760000         4.9